In [1]:
import os
import numpy as np
import pandas as pd
import pickle
import quandl
from datetime import datetime
import plotly.offline as py
import plotly.graph_objs as go
import plotly.figure_factory as ff
py.init_notebook_mode(connected=True)

In [2]:
quandl.ApiConfig.api_key = "t8LQxYisJ5vhf91FQHno"
def get_quandl_data(quandl_id):
    '''Download and cache Quandl dataseries'''
    cache_path = '{}.pkl'.format(quandl_id).replace('/','-')
    try:
        f = open(cache_path, 'rb')
        df = pickle.load(f)   
        print('Loaded {} from cache'.format(quandl_id))
    except (OSError, IOError) as e:
        print('Downloading {} from Quandl'.format(quandl_id))
        df = quandl.get(quandl_id, returns="pandas")
        df.to_pickle(cache_path)
        print('Cached {} at {}'.format(quandl_id, cache_path))
    return df

In [3]:
# Pull Kraken BTC price exchange data
btc_usd_price_kraken = get_quandl_data('BCHARTS/KRAKENUSD')

Loaded BCHARTS/KRAKENUSD from cache


In [4]:
btc_usd_price_kraken.head()


Open       High        Low      Close  Volume (BTC)  \
Date                                                                   
2014-01-07  874.67040  892.06753  810.00000  810.00000     15.622378   
2014-01-08  810.00000  899.84281  788.00000  824.98287     19.182756   
2014-01-09  825.56345  870.00000  807.42084  841.86934      8.158335   
2014-01-10  839.99000  857.34056  817.00000  857.33056      8.024510   
2014-01-11  858.20000  918.05471  857.16554  899.84105     18.748285   

            Volume (Currency)  Weighted Price  
Date                                           
2014-01-07       13151.472844      841.835522  
2014-01-08       16097.329584      839.156269  
2014-01-09        6784.249982      831.572913  
2014-01-10        6780.220188      844.938794  
2014-01-11       16698.566929      890.671709

In [5]:
# Chart the BTC pricing data
btc_trace = go.Scatter(x=btc_usd_price_kraken.index, y=btc_usd_price_kraken['Weighted Price'])
py.iplot([btc_trace])

In [6]:
# Pull Pricing Data From More BTC Exchanges
# Noticed a hitch in this dataset - there are a few notable down-spikes, particularly in late 2014 and 
# early 2016. These spikes are specific to the Kraken dataset, and we obviously don't want them to be reflected in our 
# overall pricing analysis.

# The nature of Bitcoin exchanges is that the pricing is determined by supply and demand, hence no single exchange 
# contains a true "master price" of Bitcoin. To solve this issue, along with that of down-spikes, we'll pull data from 
# three more major Bitcoin changes to calculate an aggregate Bitcoin price index.

In [7]:
# Pull pricing data for 3 more BTC exchanges
exchanges = ['COINBASE','BITSTAMP','ITBIT']

exchange_data = {}

exchange_data['KRAKEN'] = btc_usd_price_kraken

for exchange in exchanges:
    exchange_code = 'BCHARTS/{}USD'.format(exchange)
    btc_exchange_df = get_quandl_data(exchange_code)
    exchange_data[exchange] = btc_exchange_df

Cached BCHARTS/COINBASEUSD at BCHARTS-COINBASEUSD.pkl
Cached BCHARTS/BITSTAMPUSD at BCHARTS-BITSTAMPUSD.pkl
Cached BCHARTS/ITBITUSD at BCHARTS-ITBITUSD.pkl


In [ ]:
# Merge All Of The Pricing Data Into A Single Dataframe
# Define a simple function to merge a common column of each dataframe into a new combined dataframe.

In [8]:
def merge_dfs_on_column(dataframes, labels, col):
    '''Merge a single column of each dataframe into a new combined dataframe'''
    series_dict = {}
    for index in range(len(dataframes)):
        series_dict[labels[index]] = dataframes[index][col]
        
    return pd.DataFrame(series_dict)

In [10]:
# Merge the BTC price dataseries' into a single dataframe
btc_usd_datasets = merge_dfs_on_column(list(exchange_data.values()), list(exchange_data.keys()), 'Weighted Price')
btc_usd_datasets.tail()

BITSTAMP     COINBASE        ITBIT       KRAKEN
Date                                                          
2018-08-14  6044.381950  6064.944454  6048.473368  6083.281251
2018-08-15  6405.883484  6398.476867  6411.165143  6399.840013
2018-08-16  6345.799680  6346.968070  6342.792921  6347.361400
2018-08-17  6474.701714  6481.433624  6481.742317  6469.824666
2018-08-18  6437.674848  6452.522438  6426.404880          NaN

In [32]:
# Visualize The Pricing Datasets
# To visualize how these pricing datasets compare. 
# Define a helper function to provide a single-line command to compare each column in the dataframe on a graph 
# using Plotly.

In [13]:
def df_scatter(df, title, seperate_y_axis=False, y_axis_label='', scale='linear', initial_hide=False):
    '''Generate a scatter plot of the entire dataframe'''
    label_arr = list(df)
    series_arr = list(map(lambda col: df[col], label_arr))
    
    layout = go.Layout(
        title=title,
        legend=dict(orientation="h"),
        xaxis=dict(type='date'),
        yaxis=dict(
            title=y_axis_label,
            showticklabels= not seperate_y_axis,
            type=scale
        )
    )
    
    y_axis_config = dict(
        overlaying='y',
        showticklabels=False,
        type=scale )
    
    visibility = True
    if initial_hide:
        visibility = 'legendonly'
        
    # Form Trace For Each Series
    trace_arr = []
    for index, series in enumerate(series_arr):
        trace = go.Scatter(
            x=series.index, 
            y=series, 
            name=label_arr[index],
            visible=visibility
        )
        
        # Add seperate axis for the series
        if seperate_y_axis:
            trace['yaxis'] = 'y{}'.format(index + 1)
            layout['yaxis{}'.format(index + 1)] = y_axis_config    
        trace_arr.append(trace)

    fig = go.Figure(data=trace_arr, layout=layout)
    py.iplot(fig)

In [14]:
# Plot all of the BTC exchange prices
df_scatter(btc_usd_datasets, 'Bitcoin Price (USD) By Exchange')

In [ ]:
# Clean and Aggregate the Pricing Data
# We can see that, although the four series follow roughly the same path, there are various irregularities in each 
# that want to get rid of.

# Remove all of the zero values from the dataframe, since we know that the price of Bitcoin has never been 
# equal to zero in the timeframe that we are examining.

In [15]:
# Remove "0" values
btc_usd_datasets.replace(0, np.nan, inplace=True)

In [16]:
# Plot the revised dataframe
df_scatter(btc_usd_datasets, 'Bitcoin Price (USD) By Exchange')

In [17]:
# We can now calculate a new column, containing the daily average Bitcoin price across all of the exchanges.

# Calculate the average BTC price as a new column
btc_usd_datasets['avg_btc_price_usd'] = btc_usd_datasets.mean(axis=1)

In [18]:
# This new column is our Bitcoin pricing index! Chart that column to make sure it looks ok.

# Plot the average BTC price
btc_trace = go.Scatter(x=btc_usd_datasets.index, y=btc_usd_datasets['avg_btc_price_usd'])
py.iplot([btc_trace])

In [ ]:
# Cam use this aggregate pricing series later on, in order to convert the exchange rates of other 
# cryptocurrencies to USD.

In [ ]:
# Retrieve Altcoin Pricing Data
# Now that we have a solid time series dataset for the price of Bitcoin, pull in some data on non-Bitcoin 
# cryptocurrencies, commonly referred to as altcoins.

In [ ]:
# Define Poloniex API Helper Functions
# For retrieving data on cryptocurrencies we'll be using the Poloniex API. To assist in the altcoin data retrieval, 
# Define two helper functions to download and cache JSON data from this API.

# First, define get_json_data, which will download and cache JSON data from a provided URL.

In [19]:
def get_json_data(json_url, cache_path):
    '''Download and cache JSON data, return as a dataframe.'''
    try:        
        f = open(cache_path, 'rb')
        df = pickle.load(f)   
        print('Loaded {} from cache'.format(json_url))
    except (OSError, IOError) as e:
        print('Downloading {}'.format(json_url))
        df = pd.read_json(json_url)
        df.to_pickle(cache_path)
        print('Cached response at {}'.format(json_url, cache_path))
    return df

In [20]:
base_polo_url = 'https://poloniex.com/public?command=returnChartData&currencyPair={}&start={}&end={}&period={}'
start_date = datetime.strptime('2015-01-01', '%Y-%m-%d') # get data from the start of 2015
end_date = datetime.now() # up until today
pediod = 86400 # pull daily data (86,400 seconds per day)

def get_crypto_data(poloniex_pair):
    '''Retrieve cryptocurrency data from poloniex'''
    json_url = base_polo_url.format(poloniex_pair, start_date.timestamp(), end_date.timestamp(), pediod)
    data_df = get_json_data(json_url, poloniex_pair)
    data_df = data_df.set_index('date')
    return data_df
# This function will take a cryptocurrency pair string (such as 'BTC_ETH') and return the dataframe containing the 
# historical exchange rate of the two currencies.

In [33]:
#  Download Trading Data From Poloniex
# Most altcoins cannot be bought directly with USD; to acquire these coins individuals often buy Bitcoins and then trade 
# the Bitcoins for altcoins on cryptocurrency exchanges. For this reason we'll be downloading the exchange rate to BTC 
# for each coin, and then we'll use our existing BTC pricing data to convert this value to USD.

# Download exchange data for nine of the top cryptocurrencies - 
# Ethereum, Litecoin, Ripple, Ethereum Classic, Stellar, Dashcoin, Siacoin, Monero, and NEM.

In [21]:
altcoins = ['ETH','LTC','XRP','ETC','STR','DASH','SC','XMR','XEM']

altcoin_data = {}
for altcoin in altcoins:
    coinpair = 'BTC_{}'.format(altcoin)
    crypto_price_df = get_crypto_data(coinpair)
    altcoin_data[altcoin] = crypto_price_df

Cached response at https://poloniex.com/public?command=returnChartData&currencyPair=BTC_ETH&start=1420066800.0&end=1534702546.617485&period=86400
Cached response at https://poloniex.com/public?command=returnChartData&currencyPair=BTC_LTC&start=1420066800.0&end=1534702546.617485&period=86400
Cached response at https://poloniex.com/public?command=returnChartData&currencyPair=BTC_XRP&start=1420066800.0&end=1534702546.617485&period=86400
Cached response at https://poloniex.com/public?command=returnChartData&currencyPair=BTC_ETC&start=1420066800.0&end=1534702546.617485&period=86400
Cached response at https://poloniex.com/public?command=returnChartData&currencyPair=BTC_STR&start=1420066800.0&end=1534702546.617485&period=86400
Cached response at https://poloniex.com/public?command=returnChartData&currencyPair=BTC_DASH&start=1420066800.0&end=1534702546.617485&period=86400
Cached response at https://poloniex.com/public?command=returnChartData&currencyPair=BTC_SC&start=1420066800.0&end=153470254

In [22]:
altcoin_data['ETH'].tail()


close      high       low      open   quoteVolume       volume  \
date                                                                            
2018-08-15  0.044775  0.046339  0.043987  0.044979  26791.940167  1214.013592   
2018-08-16  0.045400  0.046505  0.044472  0.044775  17477.998975   795.763658   
2018-08-17  0.048156  0.048530  0.045297  0.045400  13357.452222   626.433852   
2018-08-18  0.045990  0.048675  0.044822  0.048156  14264.406892   663.471089   
2018-08-19  0.046221  0.047500  0.045500  0.045990   6785.531945   314.896851   

            weightedAverage  
date                         
2018-08-15         0.045313  
2018-08-16         0.045529  
2018-08-17         0.046898  
2018-08-18         0.046512  
2018-08-19         0.046407

In [ ]:
# Convert Prices to USD
# Since we now have the exchange rate for each cryptocurrency to Bitcoin, and we have the Bitcoin/USD historical pricing 
# index, we can directly calculate the USD price series for each altcoin

In [23]:
# Calculate USD Price as a new column in each altcoin dataframe
for altcoin in altcoin_data.keys():
    altcoin_data[altcoin]['price_usd'] =  altcoin_data[altcoin]['weightedAverage'] * btc_usd_datasets['avg_btc_price_usd']

In [ ]:
# Here, we've created a new column in each altcoin dataframe with the USD prices for that coin.

# we can re-use our merge_dfs_on_column function from earlier to create a combined dataframe of the USD price 
# for each cryptocurrency.

In [24]:
# Merge USD price of each altcoin into single dataframe 
combined_df = merge_dfs_on_column(list(altcoin_data.values()), list(altcoin_data.keys()), 'price_usd')

In [25]:
# Add the Bitcoin prices as a final column to the combined dataframe.

# Add BTC price to the dataframe
combined_df['BTC'] = btc_usd_datasets['avg_btc_price_usd']

In [ ]:
# Now we have a single dataframe containing daily USD prices for the ten cryptocurrencies that we're examining.

# reuse our df_scatter function from earlier to chart all of the cryptocurrency prices against each other.

In [26]:
# Chart all of the altocoin prices
df_scatter(combined_df, 'Cryptocurrency Prices (USD)', seperate_y_axis=False, y_axis_label='Coin Value (USD)', scale='log')

In [ ]:
# This graph gives a pretty solid "big picture" view of how the exchange rates of each currency have varied over the 
# past few years.

In [ ]:
# Compute Correlation Values of The Cryptocurrencies
# Notice that the cryptocurrency exchange rates, despite their wildly different values and volatility, 
# seem to be slightly correlated. Especially since the spike in April 2017, even many of the smaller fluctuations 
# appear to be occurring in sync across the entire market.

# A visually-derived hunch is not much better than a guess until we have the stats to back it up.

# We can test our correlation hypothesis using the Pandas corr() method, which computes a Pearson correlation 
# coefficient for each column in the dataframe against each other column.

# Computing correlations directly on a non-stationary time series (such as raw pricing data) can give biased 
# correlation values. We will work around this by using the pct_change() method, which will convert each cell in the 
# dataframe from an absolute price value to a daily return percentage.

# First we'll calculate correlations for 2016.

In [27]:
# Calculate the pearson correlation coefficients for altcoins in 2016
combined_df_2016 = combined_df[combined_df.index.year == 2016]
combined_df_2016.pct_change().corr(method='pearson')

DASH       ETC       ETH       LTC        SC       STR       XEM  \
DASH  1.000000  0.003992  0.122695 -0.012194  0.026602  0.058083  0.014571   
ETC   0.003992  1.000000 -0.181991 -0.131079 -0.008066 -0.102654 -0.080938   
ETH   0.122695 -0.181991  1.000000 -0.064652  0.169642  0.035093  0.043205   
LTC  -0.012194 -0.131079 -0.064652  1.000000  0.012253  0.113523  0.160667   
SC    0.026602 -0.008066  0.169642  0.012253  1.000000  0.143252  0.106153   
STR   0.058083 -0.102654  0.035093  0.113523  0.143252  1.000000  0.225132   
XEM   0.014571 -0.080938  0.043205  0.160667  0.106153  0.225132  1.000000   
XMR   0.121537 -0.105898  0.087216  0.129475  0.047910  0.027998  0.016438   
XRP   0.088657 -0.054095  0.085630  0.053712  0.021098  0.320116  0.101326   
BTC  -0.014040 -0.170538 -0.006502  0.750174  0.035116  0.079075  0.227674   

           XMR       XRP       BTC  
DASH  0.121537  0.088657 -0.014040  
ETC  -0.105898 -0.054095 -0.170538  
ETH   0.087216  0.085630 -0.006502  
LTC   0.129475  0.053712  0.750174  
SC    0.047910  0.021098  0.035116  
STR   0.027998  0.320116  0.079075  
XEM   0.016438  0.101326  0.227674  
XMR   1.000000  0.027649  0.127520  
XRP   0.027649  1.000000  0.044161  
BTC   0.127520  0.044161  1.000000

In [ ]:
# These correlation coefficients are all over the place. Coefficients close to 1 or -1 mean that the series' are 
# strongly correlated or inversely correlated respectively, and coefficients close to zero mean that the values tend 
# to fluctuate independently of each other.

# To help visualize these results, create one more helper visualization function.

In [28]:
def correlation_heatmap(df, title, absolute_bounds=True):
    '''Plot a correlation heatmap for the entire dataframe'''
    heatmap = go.Heatmap(
        z=df.corr(method='pearson').as_matrix(),
        x=df.columns,
        y=df.columns,
        colorbar=dict(title='Pearson Coefficient'),
    )
    
    layout = go.Layout(title=title)
    
    if absolute_bounds:
        heatmap['zmax'] = 1.0
        heatmap['zmin'] = -1.0
        
    fig = go.Figure(data=[heatmap], layout=layout)
    py.iplot(fig)

In [29]:
correlation_heatmap(combined_df_2016.pct_change(), "Cryptocurrency Correlations in 2016")

In [ ]:
# Here, the dark red values represent strong correlations (note that each currency is, obviously, strongly correlated 
# with itself), and the dark blue values represent strong inverse correlations. 
# All of the light blue/orange/gray/tan colors in-between represent varying degrees of weak/non-existent correlations.

# What does this chart tell us? Essentially, it shows that there was very little statistically significant linkage 
# between how the prices of different cryptocurrencies fluctuated during 2016.

# Now, to test our hypothesis that the cryptocurrencies have become more correlated in recent months, 
# let's repeat the same test using only the data from 2017.

In [30]:
combined_df_2017 = combined_df[combined_df.index.year == 2017]
combined_df_2017.pct_change().corr(method='pearson')

DASH       ETC       ETH       LTC        SC       STR       XEM  \
DASH  1.000000  0.387555  0.506911  0.340153  0.291424  0.183038  0.325968   
ETC   0.387555  1.000000  0.601437  0.482062  0.298406  0.210387  0.321852   
ETH   0.506911  0.601437  1.000000  0.437609  0.373078  0.259399  0.399200   
LTC   0.340153  0.482062  0.437609  1.000000  0.339144  0.307589  0.379088   
SC    0.291424  0.298406  0.373078  0.339144  1.000000  0.402966  0.331350   
STR   0.183038  0.210387  0.259399  0.307589  0.402966  1.000000  0.339502   
XEM   0.325968  0.321852  0.399200  0.379088  0.331350  0.339502  1.000000   
XMR   0.498418  0.447398  0.554632  0.437204  0.378644  0.327488  0.336076   
XRP   0.091146  0.114780  0.212350  0.323905  0.243872  0.509828  0.268168   
BTC   0.307095  0.416562  0.410771  0.420645  0.325318  0.230957  0.329431   

           XMR       XRP       BTC  
DASH  0.498418  0.091146  0.307095  
ETC   0.447398  0.114780  0.416562  
ETH   0.554632  0.212350  0.410771  
LTC   0.437204  0.323905  0.420645  
SC    0.378644  0.243872  0.325318  
STR   0.327488  0.509828  0.230957  
XEM   0.336076  0.268168  0.329431  
XMR   1.000000  0.226636  0.409183  
XRP   0.226636  1.000000  0.131469  
BTC   0.409183  0.131469  1.000000

In [31]:
# It is notable, however, that almost all of the cryptocurrencies have become more correlated with each other 
# across the board.

correlation_heatmap(combined_df_2017.pct_change(), "Cryptocurrency Correlations in 2017")

In [34]:
# The most immediate explanation is that hedge funds have recently begun publicly trading in 
# crypto-currency markets12. These funds have vastly more capital to play with than the average trader, so if a 
# fund is hedging their bets across multiple cryptocurrencies, and using similar trading strategies for each based 
# on independent variables (say, the stock market), it could make sense that this trend would emerge.

# In-Depth - XRP and STR
# For instance, one noticeable trait of the above chart is that XRP (the token for Ripple), is the least correlated 
# cryptocurrency. The notable exception here is with STR (the token for Stellar, officially known as "Lumens"), 
# which has a stronger (0.62) correlation with XRP.

# What is interesting here is that Stellar and Ripple are both fairly similar fintech platforms aimed at reducing the 
# friction of international money transfers between banks.

# It is conceivable that some big-money players and hedge funds might be using similar trading strategies for their 
# investments in Stellar and Ripple, due to the similarity of the blockchain services that use each token. 
# This could explain why XRP is so much more heavily correlated with STR than with the other cryptocurrencies.

In [ ]:
# Here are some ideas:

# Add data from more cryptocurrencies to the analysis.
# Adjust the time frame and granularity of the correlation analysis, for a more fine or coarse grained view of the trends.
# Search for trends in trading volume and/or blockchain mining data sets. The buy/sell volume ratios are likely more relevant than the raw price data if you want to predict future price fluctuations.
# Add pricing data on stocks, commodities, and fiat currencies to determine which of them correlate with cryptocurrencies (but please remember the old adage that "Correlation does not imply causation").
# Quantify the amount of "buzz" surrounding specific cryptocurrencies using Event Registry, GDLELT, and Google Trends.
# Train a predictive machine learning model on the data to predict tomorrow's prices. If you're more ambitious, you could even try doing this with a recurrent neural network (RNN).
# Use your analysis to create an automated "Trading Bot" on a trading site such as Poloniex or Coinbase, using their respective trading APIs. Be careful: a poorly optimized trading bot is an easy way to lose your money quickly.